In [1]:
import pandas as pd

# Defining the data
positions = [
    "Python研发工程师", "云端开发工程师", "语音算法工程师", "运维顾问", "Java架构师",
    "诊断开发工程师"
]
scores = {
    "A": [65, 70, 45, 85, 77, 95],
    "B": [55, 80, 65, 66, 90, 65],
    "C": [85, 77, 95, 66, 90, 65],
    "D": [67, 80, 93, 95, 90, 95],
    "E": [66, 90, 65, 95, 90, 95],
    "F": [69, 72, 85, 66, 90, 65],
    "G": [85, 74, 55, 95, 92, 85],
    "H": [95, 90, 95, 69, 82, 85],
    "I": [86, 90, 65, 69, 92, 85],
    "J": [69, 92, 85, 95, 92, 85],
    "K": [85, 74, 95, 85, 74, 95],
    "L": [95, 92, 85, 65, 69, 92]
}

# Creating the DataFrame
df = pd.DataFrame(scores, index=positions)
df


A   B   C   D   E   F   G   H   I   J   K   L
Python研发工程师  65  55  85  67  66  69  85  95  86  69  85  95
云端开发工程师      70  80  77  80  90  72  74  90  90  92  74  92
语音算法工程师      45  65  95  93  65  85  55  95  65  85  95  85
运维顾问         85  66  66  95  95  66  95  69  69  95  85  65
Java架构师      77  90  90  90  90  90  92  82  92  92  74  69
诊断开发工程师      95  65  65  95  95  65  85  85  85  85  95  92

In [3]:
data = df.T

In [4]:
data

Python研发工程师  云端开发工程师  语音算法工程师  运维顾问  Java架构师  诊断开发工程师
A           65       70       45    85       77       95
B           55       80       65    66       90       65
C           85       77       95    66       90       65
D           67       80       93    95       90       95
E           66       90       65    95       90       95
F           69       72       85    66       90       65
G           85       74       55    95       92       85
H           95       90       95    69       82       85
I           86       90       65    69       92       85
J           69       92       85    95       92       85
K           85       74       95    85       74       95
L           95       92       85    65       69       92

In [5]:
from itertools import permutations

In [7]:
list(permutations(['A','B','C','D'],3))

[('A', 'B', 'C'),
 ('A', 'B', 'D'),
 ('A', 'C', 'B'),
 ('A', 'C', 'D'),
 ('A', 'D', 'B'),
 ('A', 'D', 'C'),
 ('B', 'A', 'C'),
 ('B', 'A', 'D'),
 ('B', 'C', 'A'),
 ('B', 'C', 'D'),
 ('B', 'D', 'A'),
 ('B', 'D', 'C'),
 ('C', 'A', 'B'),
 ('C', 'A', 'D'),
 ('C', 'B', 'A'),
 ('C', 'B', 'D'),
 ('C', 'D', 'A'),
 ('C', 'D', 'B'),
 ('D', 'A', 'B'),
 ('D', 'A', 'C'),
 ('D', 'B', 'A'),
 ('D', 'B', 'C'),
 ('D', 'C', 'A'),
 ('D', 'C', 'B')]

In [10]:
people = list(data.index)
positions = list(data.columns)

In [11]:
positions

['Python研发工程师', '云端开发工程师', '语音算法工程师', '运维顾问', 'Java架构师', '诊断开发工程师']

In [12]:
score_best = 0
best_team = None
for team in permutations(people,6):
    score = 0
    for i in range(6):
        score += data.loc[team[i],positions[i]]
    if score > score_best:
        score_best = score
        best_team = list(team)


In [13]:
best_team

['H', 'J', 'C', 'D', 'G', 'A']

In [14]:
score_best

564

In [15]:
import pulp as lp

In [16]:
data

Python研发工程师  云端开发工程师  语音算法工程师  运维顾问  Java架构师  诊断开发工程师
A           65       70       45    85       77       95
B           55       80       65    66       90       65
C           85       77       95    66       90       65
D           67       80       93    95       90       95
E           66       90       65    95       90       95
F           69       72       85    66       90       65
G           85       74       55    95       92       85
H           95       90       95    69       82       85
I           86       90       65    69       92       85
J           69       92       85    95       92       85
K           85       74       95    85       74       95
L           95       92       85    65       69       92

In [17]:
I = list(data.index)
J = list(data.columns)

In [18]:
I

['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L']

In [19]:
J

['Python研发工程师', '云端开发工程师', '语音算法工程师', '运维顾问', 'Java架构师', '诊断开发工程师']

In [20]:
model = lp.LpProblem('POSITION',sense=lp.LpMaximize) # 模型初始化

In [21]:
x = lp.LpVariable.dicts('x',indices=[(i,j) for i in I for j in J],cat='Binary')

In [23]:
obj = lp.lpSum(data.loc[i,j]*x[i,j] for i in I for j in J)

In [24]:
model += obj # 先添加目标函数

In [25]:
for j in J:
    model += lp.lpSum(x[i,j] for i in I) == 1,f'position_{j}'
for i in I:
    model += lp.lpSum(x[i,j] for j in J) <=1 ,f'people_{i}'

In [26]:
model.solve()

1

In [27]:
lp.value(model.objective)

564.0

In [29]:
for i in I:
    for j in J:
        if lp.value(x[i,j])>0:
            print(i,j)

A 诊断开发工程师
C 语音算法工程师
D 运维顾问
G Java架构师
H Python研发工程师
J 云端开发工程师


In [30]:
model

POSITION:
MAXIMIZE
77*x_('A',_'Java架构师') + 65*x_('A',_'Python研发工程师') + 70*x_('A',_'云端开发工程师') + 95*x_('A',_'诊断开发工程师') + 45*x_('A',_'语音算法工程师') + 85*x_('A',_'运维顾问') + 90*x_('B',_'Java架构师') + 55*x_('B',_'Python研发工程师') + 80*x_('B',_'云端开发工程师') + 65*x_('B',_'诊断开发工程师') + 65*x_('B',_'语音算法工程师') + 66*x_('B',_'运维顾问') + 90*x_('C',_'Java架构师') + 85*x_('C',_'Python研发工程师') + 77*x_('C',_'云端开发工程师') + 65*x_('C',_'诊断开发工程师') + 95*x_('C',_'语音算法工程师') + 66*x_('C',_'运维顾问') + 90*x_('D',_'Java架构师') + 67*x_('D',_'Python研发工程师') + 80*x_('D',_'云端开发工程师') + 95*x_('D',_'诊断开发工程师') + 93*x_('D',_'语音算法工程师') + 95*x_('D',_'运维顾问') + 90*x_('E',_'Java架构师') + 66*x_('E',_'Python研发工程师') + 90*x_('E',_'云端开发工程师') + 95*x_('E',_'诊断开发工程师') + 65*x_('E',_'语音算法工程师') + 95*x_('E',_'运维顾问') + 90*x_('F',_'Java架构师') + 69*x_('F',_'Python研发工程师') + 72*x_('F',_'云端开发工程师') + 65*x_('F',_'诊断开发工程师') + 85*x_('F',_'语音算法工程师') + 66*x_('F',_'运维顾问') + 92*x_('G',_'Java架构师') + 85*x_('G',_'Python研发工程师') + 74*x_('G',_'云端开发工程师') + 85*x_('G',_'诊断开发工程师') + 55*x_('G',_

## 运输

In [32]:
import pandas as pd

# Data
data = {
    "V1": [6, 4, 5, 7, 2, 5],
    'V2': [2, 9, 2, 6, 3, 5],
    "V3": [6, 9, 2, 6, 9, 2],
    "V4": [7, 5, 1, 7, 5, 2],
    "V5": [4, 3, 9, 3, 7, 8],
    "V6": [2, 8, 4, 9, 2, 1],
    "V7": [5, 5, 3, 2, 6, 4],
    "V8": [9, 8, 3, 7, 5, 3],
    "存货": [60, 55, 51, 43, 41, 52]
}

# Creating the DataFrame
df = pd.DataFrame(data, index=["W1", "W2", "W3", "W4", "W5", "W6"])

# Demand
demand = {"V1": 35,"V2":37, "V3": 22, "V4": 32, "V5": 41, "V6": 32, "V7": 43, "V8": 38}

# Adding demand as a row
df = df.append(demand, ignore_index=True)
df.index = ["W1", "W2", "W3", "W4", "W5", "W6", "需求量"]

df


C:\Users\Haihua Wang\AppData\Local\Temp\ipykernel_14752\2947346913.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(demand, ignore_index=True)


V1  V2  V3  V4  V5  V6  V7  V8    存货
W1    6   2   6   7   4   2   5   9  60.0
W2    4   9   9   5   3   8   5   8  55.0
W3    5   2   2   1   9   4   3   3  51.0
W4    7   6   6   7   3   9   2   7  43.0
W5    2   3   9   5   7   2   6   5  41.0
W6    5   5   2   2   8   1   4   3  52.0
需求量  35  37  22  32  41  32  43  38   NaN